In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib notebook

In [2]:
train9 = pd.read_csv('train/train9_enc.csv')
train1 = pd.read_csv('train/train1_enc.csv')
test9 = pd.read_csv('test/test9_enc.csv')
test1 = pd.read_csv('test/test1_enc.csv')

In [86]:
features = ['f1', 'f2', 'f3', 'f4']
target_name = 'kda_ratio'

In [4]:
train9.head()

user_id     id  num_games  num_wins    kda_ratio        f1        f2  \
0        1   1_74        304       185  3743.699732  0.092123  0.715667   
1        1   1_65        255       151  4009.021513 -0.345066  1.163758   
2        1   1_39        203       135  5094.621514  0.549268  0.607199   
3        1  1_106        158       106  4619.212963  0.692378  0.137812   
4        1    1_2        157        94  2871.627907 -0.541217  0.310945   

         f3        f4  hero_id  
0  0.001144 -0.393678     74.0  
1  0.539587 -0.801640     65.0  
2 -0.197010 -0.806031     39.0  
3  1.358986 -1.285956    106.0  
4  1.998080 -0.535615      2.0

In [6]:
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import RidgeCV
from sklearn.metrics import mean_squared_error
from sklearn.linear_model import Ridge
import math

In [40]:
from sklearn.linear_model import LassoCV
from sklearn.linear_model import ElasticNetCV
from sklearn.linear_model import BayesianRidge

In [64]:
import xgboost as xgb

C:\Users\admin\Anaconda3\lib\site-packages\sklearn\cross_validation.py:44: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [22]:
alphas1 = np.arange(0.1,1,0.1)

In [23]:
alphas2 = np.arange(1,10,0.5)

In [25]:
alphas = []
for i in alphas1:
    alphas.append(i)
for i in alphas2:
    alphas.append(i)

In [27]:
alphas[2] = 0.3
alphas[6] = 0.7

In [29]:
alphas.extend([11,12,13,14,15])

In [70]:
# dict models 
train_user_models = {}

In [87]:
# linear regression
for u_id in train9['user_id'].unique():
    data = train9[train9['user_id'] == u_id]
    #train_user_models[u_id] = RidgeCV(alphas=alphas, normalize=True)
    #train_user_models[u_id] = LinearRegression(n_jobs=-1, normalize=True)
    #train_user_models[u_id] = LassoCV(alphas=alphas, normalize=True, n_jobs=-1, max_iter=5000)
    #train_user_models[u_id] = BayesianRidge(normalize=True, n_iter=1000)
    train_user_models[u_id] = ElasticNetCV(normalize=True, max_iter=2000)
    train_user_models[u_id].fit(data[features], data[target_name])

In [88]:
train_user_models[1].predict(train1[0:1][features].values)

array([3788.23836827])

In [89]:
# linear regression 
ans = []
for index,row in train1.iterrows():
    u_id = row['user_id']
    ans.append(train_user_models[u_id].predict(row[features])[0])

C:\Users\admin\Anaconda3\lib\site-packages\sklearn\utils\validation.py:395: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  DeprecationWarning)
C:\Users\admin\Anaconda3\lib\site-packages\sklearn\utils\validation.py:395: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  DeprecationWarning)
C:\Users\admin\Anaconda3\lib\site-packages\sklearn\utils\validation.py:395: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  DeprecationWarn

In [11]:
# score on linear regression
math.sqrt(mean_squared_error(train1[target_name], np.array(ans)))

1353.2959723753104

In [12]:
# mean of kda_ratio by user id 
mean_ans = train9.groupby('user_id')['kda_ratio'].mean().values

In [13]:
# score on mean of kda_ratio
math.sqrt(mean_squared_error(train1[target_name], mean_ans))

761.6660781249168

In [84]:
# score on ridge cv regression
math.sqrt(mean_squared_error(train1[target_name], np.array(ans)))

795.6693562902311

In [46]:
# score on Lasso cv regression
math.sqrt(mean_squared_error(train1[target_name], np.array(ans)))

1106.43660726055

In [55]:
# score on Bayesian ridge regression
math.sqrt(mean_squared_error(train1[target_name], np.array(ans)))

815.7982964825912

In [60]:
# score on Elastic Cv regression
math.sqrt(mean_squared_error(train1[target_name], np.array(ans)))

761.2013989390084

In [63]:
elastic_net_pred = ans

In [69]:
# score on linear regression / only hero features
math.sqrt(mean_squared_error(train1[target_name], np.array(ans)))

1267.0175227646837

In [71]:
lr_hero_f = ans

In [76]:
# score on ridge cv regresssion only hero features
print(math.sqrt(mean_squared_error(train1[target_name], np.array(ans))))
rcv_hero_f = ans

794.6781169141722


In [79]:
# ride cv hero peram coef
train_user_models[1].coef_

array([ 476.37087114,  246.02073756, -112.23083081, -361.95154854])

In [85]:
# ridge cv all peram coef
train_user_models[1].coef_

array([   1.12497798,  455.8333619 ,  195.09381776,  -90.96020954,
       -393.34522536])

In [90]:
# score on Elastic Cv regression/ only hero features
print(math.sqrt(mean_squared_error(train1[target_name], np.array(ans))))
ecv_hero_f = ans

759.0768434316525


In [62]:
for u_id in train9['user_id'].unique():
    #print("{0} : {1}".format(u_id,train_user_models[u_id].alpha_))
    print(train_user_models[u_id].alphas_)

[278.23662194 259.48440485 241.99602443 225.68630231 210.47580088
 196.29043634 183.06111789 170.72341123 159.21722471 148.48651664
 138.47902239 129.14599975 120.44199161 112.32460448 104.75430207
  97.69421271  91.10994975  84.96944407  79.24278792  73.90208923
  68.92133576  64.2762684   59.94426304  55.90422033  52.13646299
  48.62263988  45.34563668  42.28949254  39.43932228  36.78124396
  34.30231122  31.99045025  29.83440097  27.82366219  25.94844049
  24.19960244  22.56863023  21.04758009  19.62904363  18.30611179
  17.07234112  15.92172247  14.84865166  13.84790224  12.91459998
  12.04419916  11.23246045  10.47543021   9.76942127   9.11099497
   8.49694441   7.92427879   7.39020892   6.89213358   6.42762684
   5.9944263    5.59042203   5.2136463    4.86226399   4.53456367
   4.22894925   3.94393223   3.6781244    3.43023112   3.19904502
   2.9834401    2.78236622   2.59484405   2.41996024   2.25686302
   2.10475801   1.96290436   1.83061118   1.70723411   1.59217225
   1.48486

In [ ]:
# dict models 
train_user_models = {}
features1 = ['f1', 'f2', 'f3', 'f4']

In [ ]:
# linear regression
for u_id in all_data['user_id'].unique():
    data = all_data[all_data['user_id'] == u_id]
    train_user_models[u_id] = ElasticNetCV(normalize=True, max_iter=1000)
    train_user_models[u_id].fit(data[features], data[target_name])

In [ ]:
# linear regression for all data
ans = []
for index,row in train1.iterrows():
    u_id = row['user_id']
    ans.append(train_user_models[u_id].predict(row[features])[0])